## Using Lets-Plot with GeoTools to Create Maps


The Let's-Plot library allows to easily visualize geospatial features from GeoTools `SimpleFeatureCollection`.

`SimpleFeatureCollection` is a collection of `SimpleFeature`-s. Each `SimpleFeature` have a "geometry" attribute as well as optional "data" attributes.

The Let's-Plot library understands the following three geometry types:

- Points / Multi-Points
- Lines / Multi-Lines
- Polygons / Multi-Polygons

These shapes can be plotted using various geometry layers, depending on the type of the shape:

- `geomPoint`, `geomText` with Points / Multi-Points
- `geomPath` with Lines / Multi-Lines
- `geomPolygon`, `geomMap` with Polygons / Multi-Polygons
- `geomRect` when used with Polygon shapes will display corresponding bounding boxes

Apart from `SimpleFeatureCollection` the Lets-Plot library can also plot an individual `Geometry` (org.locationtech.jts.geom) and a `ReferencedEnvelope` (org.geotools.geometry.jts).

Before passing to a Lets-Plot geometry layer (via `map` or `data` parameters) any 'foreign' object must be converted to a Lets-Plot `SpatialDataset` object. This is done by the `toSpatialDataset()` extension method provided by Lets-Plot GeoTools extension (see the `%use lets-plot-gt` 'magic').


Shapfiles used in this tutorial:
- naturalearth_lowres.shp
- naturalearth_cities.shp 

all are the copies of shapefiles distributed with the [GeoPandas](https://geopandas.org/) Python package.

In [1]:
%useLatestDescriptors
%use lets-plot

In [2]:
// Initialize Lets-Plot GeoTools extension. 
%use lets-plot-gt

In [3]:
LetsPlot.getInfo()

Lets-Plot Kotlin API v.4.11.0. Frontend: Notebook with dynamically loaded JS. Lets-Plot JS v.4.7.0.

In [4]:
@file:DependsOn("org.geotools:gt-shapefile:[30,)")
@file:DependsOn("org.geotools:gt-cql:[30,)")

In [5]:
import org.geotools.data.shapefile.ShapefileDataStoreFactory
import org.geotools.data.simple.SimpleFeatureCollection
import java.net.URL

val factory = ShapefileDataStoreFactory()

### Polygon shapes - Naturalearth low-resolution world dataset.

In [6]:
val worldFeatures : SimpleFeatureCollection = with("naturalearth_lowres") {
    val url = "https://raw.githubusercontent.com/JetBrains/lets-plot-kotlin/master/docs/examples/shp/${this}/${this}.shp"
    factory.createDataStore(URL(url)).featureSource.features
}

// Convert Feature Collection to SpatialDataset.
// Use 10 decimals to encode floating point numbers (this is the default).
val world = worldFeatures.toSpatialDataset(10)

In [7]:
world["continent"]?.distinct()

[Oceania, Africa, North America, Asia, South America, Europe, Seven seas (open ocean), Antarctica]

#### geomPolygon()

In [8]:
val voidTheme = theme(axis="blank", panelGrid="blank")

// Use the parameter `map` in `geomPolygon()` to display Polygons / Multi-Polygons 
letsPlot() + 
    geomPolygon(map = world, fill = "white", color = "gray") + 
    ggsize(700, 400) + 
    voidTheme

#### geomMap()

*geomMap()* is very similar to *geomPolygon()* but it automatically applies the `Mercator` projection and other defaults that are more suitable for displaying blank maps. 

In [9]:
letsPlot() + 
    geomMap(map = world) + 
    ggsize(700, 400) + 
    voidTheme

In [10]:
// When applying Mercator projection to the world map, Antarctica becomes disproportionally large so 
// in the future let's show only part of it above 85-th parallel south:
val worldLimits = coordMap(ylim = -70 to 85)

### Point shapes - Naturalearth world capitals dataset.

In [11]:
val cityFeatures : SimpleFeatureCollection = with("naturalearth_cities") {
    val url = "https://raw.githubusercontent.com/JetBrains/lets-plot-kotlin/master/docs/examples/shp/${this}/${this}.shp"
    factory.createDataStore(URL(url)).featureSource.features
}

#### geomPoint()

In [12]:
// Use parameter `map` in `geomPoint()` to display Point shapes
val cities = cityFeatures.toSpatialDataset(10)
letsPlot() + 
    geomMap(map = world) + 
    geomPoint(map = cities, color = "red") +
    ggsize(800, 600) + voidTheme + worldLimits

### geomText()

The situation with *geomText()* is different because in order to display labels we have to specify mapping for the aesthetic "label".

Aesthetic mapping binds a variable in *data* (passed via `data` parameter) with its representation on the screen.

Variables in a SpatialDataset passed via the `map` parameter can not be used in the aesthetic mapping.

Fortunately, such a SpatialDataset can as well be passed via the `data` parameter and Lets-Plot will undersand that its *geometries* should be mapped to the "x" and "y" aesthetic automatically.

In the next example we are going to show names of cities as labels on map. 

Let's only show South American capitals because too many labels on the entire world map would quickly become not legible.

In [13]:
import org.geotools.filter.text.cql2.CQL

In [14]:
// Obtain bounding box of South America and use it to set the limits.
val southAm = worldFeatures.subCollection(
    CQL.toFilter("continent = 'South America'")
)
val southAmBounds = southAm.bounds

// Let's use slightly expanded boundind box.
southAmBounds.expandBy(4.0)

// Define limits to use later with city markers and labels. 
val southAmLimits = coordMap(
    xlim = southAmBounds.minX to southAmBounds.maxX,
    ylim = southAmBounds.minY to southAmBounds.maxY
)


letsPlot() + 
    geomMap(map = southAm.toSpatialDataset()) +
    geomRect(map = southAmBounds.toSpatialDataset(), alpha = 0, color = "#EFC623")

<path d="M66.8350013430852 283.63873916153585 L66.8350013430852 283.63873916153585 L69.86318472578671 290.5864578426611 L74.31634406105775 294.0958853134524 L79.11205411442657 295.5733280566357 L77.57057588298656 298.5557549548811 L74.31634406105775 298.8560509479593 L72.56960943933359 296.7428480664936 L66.83726295747005 296.58022087048744 L66.8350013430852 283.63873916153585 ZM104.5459878691332 179.48725629013532 L104.5459878691332 179.48725629013532 L102.77394928140603 186.80390802646357 L102.80749419042647 190.85151271343796 L102.06428415974094 191.76237345232897 L101.5647393923291 196.58120075660688 L105.9138058770485 200.15699068708295 L105.4461243477763 203.06242982689307 L107.58662588177617 204.91200373513607 L107.41261719784836 206.99769606342903 L104.12114469336743 212.53777518247335 L99.0421445271302 214.88385750778068 L92.17198782987091 215.79931394266976 L88.40902790965771 215.35613413362384 L89.12904858342702 217.9896586368056 L88.42761479862966 221.32685167610046 L89.05974604052474 223.59616300608332 L87.00509823175955 225.18967512280577 L83.49500851002387 225.81709324110574 L80.20105775386264 224.16482160454893 L78.87899889617478 225.35116038497776 L79.35677045107482 229.9004389993912 L81.66951048918196 231.29253593023978 L83.5448390742153 229.8344044777121 L84.56525927685254 232.24033017994418 L81.4112412416182 233.6876615646783 L78.66055869679937 236.60897298074173 L78.15694251542351 241.39953449162695 L77.34699670245553 243.98295693082733 L74.11093082913158 243.99673488942994 L71.42592195829175 246.49130295635558 L70.44364913227687 250.18430571342375 L73.81256700724563 253.83914243997103 L77.0874883293942 254.8573699931004 L75.90890255261675 259.42253864800216 L71.8630678845467 262.33364658284614 L69.63680113425173 268.49030267304323 L66.51048641459593 270.59586304977427 L65.10673375491953 273.11772125498476 L66.21309619173115 278.8022023435245 L68.49299939267746 282.02747877539457 L63.8741574910471 280.8681097117276 L55.596619265188224 280.1227302671316 L54.17640393211906 276.89883060090415 L54.2429626965222 272.8175280244142 L51.96235142337363 273.16610965459756 L50.755531277379816 271.2105255798884 L50.45619385647274 265.5771873517525 L53.08420293455683 263.2761715377737 L54.17038532045524 259.9926151471359 L53.772360370186476 257.4041394088209 L55.5882109107838 253.09088616877287 L56.83937406328562 246.53453308376587 L56.471796207436995 243.6772622842547 L57.96715567685044 242.7614426188176 L57.60055142002295 240.94918230885406 L56.01172645142728 239.99013155292033 L57.14065868223511 237.99225088569028 L55.594495049266584 236.19931688223954 L54.79472777086605 230.8102268821018 L56.17210475042876 229.86992300254437 L55.593432941305764 224.29908290675252 L57.31378227642392 215.74470681702212 L59.365155252367 214.15051380675513 L58.323935435554034 209.90320565335045 L58.31278330230796 205.95650573253727 L60.90627387235037 203.17969696367817 L60.82652726806168 199.66073174047378 L62.781602457383656 195.59449785921285 L62.790276338949525 191.80619876273434 L61.90093795745142 191.0585158103957 L60.32291108668585 184.0679858661299 L62.43323105308443 179.96341539416602 L62.10937664082377 176.1385183330186 L63.33372156782863 172.5821241732341 L65.57707055409381 168.9435844805708 L67.99442822394425 166.54825316088224 L66.96931704442301 165.04348654280346 L67.68455823271111 163.81303298596094 L67.57613471382274 157.4958995584003 L71.30723139623879 155.6424164609394 L72.48289637595275 151.76134980833956 L72.06690409963207 150.8303921757818 L74.9214962050196 147.4851747465828 L79.40359170926308 148.38469090567946 L81.41734836256424 151.06133877291086 L82.75392269525994 148.08086255494155 L86.6602671874439 148.2336140252319 L93.51095190564973 155.10044464745988 L96.3116420328819 155.67051950403646 L100.49705538612028 158.4490502069562 L104.02502392496814 159.92604006685423 L104.51677990089567 161.599312610548 L101.14432166628589 167.410976009541 L104.598650721106 168.4598166656597 L108.4456941867333 169.04898919850547

In [15]:
// Add `text` layer and use the `data` parameter to pass `cities` SpartialDataset.
// Also configure `tooltip` in the points layer to show the city name.
letsPlot() + 
    geomMap(map = southAm.toSpatialDataset(), fill="#e5f5e0") +
    geomPoint(data = cities, color = "red", size = 3, tooltips = layerTooltips().line("@name")) +
    geomText(data = cities, vjust = 1, position = positionNudge(y = -.5)) { label = "name" } +
    geomRect(map = southAmBounds.toSpatialDataset(), alpha = 0, fill = "black", color="#EFC623", size=16) +
    southAmLimits +
    ggsize(450, 691) + 
    voidTheme

<path d="M124.6996005608375 585.6688390827096 L124.6996005608375 585.6688390827096 L127.55387219202305 591.3776172636489 L131.27027272779054 600.7442740853159 L140.93291412078582 608.3591687234658 L151.33883562093462 611.5649824685504 L147.99407513874394 618.0363704043729 L140.93291412078582 618.6879645366299 L137.14278019838878 614.1026532785039 L124.70450790125022 613.7497783514134 L124.6996005608375 585.6688390827096 ZM206.52639182140717 359.67682896888664 L206.52639182140717 359.67682896888664 L202.68135235198173 375.552789517977 L202.75413942336672 384.3354423822181 L201.14149288065 386.3118640676387 L200.05756087107278 396.7679462938494 L209.49433747668257 404.52683682381763 L208.47954358244834 410.83117367401684 L213.12408853739288 414.8444523509419 L212.74651760730194 419.3700701218564 L205.60455028226176 431.39115308472066 L194.58393468187091 436.4817753780524 L179.67679674195688 438.46816898655885 L171.51177735959482 437.5065398947118 L173.07410671778115 443.2208656032849 L171.55210792700228 450.4620391544989 L172.92373131702163 455.38608070338523 L168.46547517339923 458.84374636949474 L160.84914355693655 460.20514303738014 L153.701798823305 456.61997863928343 L150.83314318345617 459.1941434833512 L151.8698308146864 469.06534829287426 L156.88810569347902 472.0859753161515 L160.9572678875391 468.9220639739213 L163.17141603403724 474.14253679525683 L156.3277028571643 477.2830137228945 L150.35916299243507 483.6217908663731 L149.26639666768187 494.01654085524865 L147.50894418299748 499.6221531222284 L140.48720035937652 499.65204908217083 L134.66116183197727 505.0648616151077 L132.52978737324412 513.0780851757959 L139.83979872865274 521.0084945727518 L146.94585264313042 523.2178850215572 L144.38851057326883 533.1235686698997 L135.6096983661081 539.4402058959488 L130.77905665004204 552.7991619764983 L123.99545522387882 557.3678902253414 L120.94953713882762 562.8399179805417 L123.35016614684866 575.1743300526127 L128.29719035660457 582.1726625190936 L118.27504437298717 579.6570176339853 L100.31411428459262 578.0396638110949 L97.23247483917953 571.0443187052011 L97.37689668074586 562.1885468264412 L92.42833606789827 562.944913045357 L89.80972994612318 558.7016093130826 L89.16021576170579 546.4781690438798 L94.86257388258741 541.4853338506753 L97.21941541735941 534.3605432227916 L96.35576512543071 528.7439661073707 L100.29586950438193 519.3848984976279 L103.0106928368865 505.15866405672045 L102.21310785560377 498.9588447779268 L105.45779802245193 496.97166301739964 L104.66232559486264 493.0393488629881 L101.21483028828777 490.95836257110534 L103.66443212869137 486.6232820181731 L100.30950507680393 482.7329028486172 L98.5741383793162 471.03944205248814 L101.56282546964042 468.9991334750155 L100.3072004729097 456.91130412720713 L102.05370608946771 446.92659545182346 L104.04008255603253 438.34968028384026 L108.49123283777135 434.8905371879663 L106.2319528651334 425.67455983749574 L106.2077545249864 417.11085412893726 L111.83521302078918 411.0856245491434 L111.66217568223101 403.4500345182791 L115.9043752148491 394.6269592908843 L115.92319614640496 386.40695796087306 L113.99347452396489 384.78460589570386 L110.56940935747787 369.6162773197571 L115.14846515237821 360.71001784039566 L114.44575302967723 352.41060479800564 L117.10238511496527 344.69379997901774 L121.97009254279772 336.79875253126113 L127.21537089997776 331.6012678205211 L124.99104408615591 328.3361656501402 L126.54300272756103 325.66627881803527 L126.30774108459963 311.95911265877487 L134.40362235236177 307.93735166834915 L136.95462676114238 299.5160596230911 L136.051990253954 297.49603090230653 L142.24599719620863 290.23744571225285 L151.97142543400724 292.1892514793884 L156.3409543299283 297.9971479702084 L159.24110622200845 291.52999269766167 L167.71724712415715 291.86143888418775 L168.91698547682245 293.57905476847037 L182.58213399317083 306.76135977484444 L188.65918228964722 307.99833076365087 L197.740857852764 314.0272966641281 L205.39598363428553 317.232127725

### Choropleth

As we saw earlier, *Lets-Plot* geom-layers accept *SpatialDataset* in their `data` parameter. 

This makes it easy to bind aesthetics with variables in *SpatialDataset*.

In [16]:
// Create choropleth by mapping the `continent` variable to the `fill` aesthetic.
letsPlot() + 
    geomMap(data = world, color = "white") { fill = "continent" } + 
    ggsize(1000, 600) + voidTheme + worldLimits

In [17]:
// Create another choropleth by mapping the `GDP estimate` variable to the `fill` aesthetic.
letsPlot() + 
    geomMap(data = world, color = "white") { fill = "gdp_md_est" } + 
    ggsize(900, 600) + voidTheme + worldLimits + labs(fill = "GDP (mil$)")

### Joining `data` and `geometry` datasets

In this example we will use both: the `data` and the `map` parameters.

We will use the `data` parameter to pass "average temperature per continent" dataset to the geom layer.

The continent geometries *SpatialDataset* is passed via the `map` parameter as before.

For this to work it is also necessary to specify fields by which *Lets-Plot* will join `data` and `map` datasets. We will do that using the *mapJoin* parameter.

In [18]:
// Average temperatures
val climateData = mapOf(
    "region" to listOf("Europe", "Asia", "North America", "Africa", "Australia", "Oceania"),
    "avg_temp" to listOf(8.6, 16.6, 11.7, 21.9, 14.9, 23.9)
)

In [19]:
// Join `data` and `map` using the `mapJoin` parameter.
// For the sake of the demo let's use `geom_rect` and customize the tooltip.
letsPlot() + geomRect(data = climateData,
                        map = world,
                        mapJoin = "region" to "continent",
                        color = "white",
                        tooltips=layerTooltips().line("^fill C\u00b0")) { fill = "avg_temp" } + 
    scaleFillGradient(low = "light_blue", high = "dark_green", name="Average t[C\u00b0]") + 
    ggsize(900, 500) + voidTheme